In [1]:
import pprint
#(indent=4, width=200, depth=None,stream=None, compact=False, sort_dicts=False)
pp = pprint.PrettyPrinter(sort_dicts=False)


In [2]:
def find_nth(haystack, needle, n):
    start = haystack.find(needle)
    while start >= 0 and n > 1:
        start = haystack.find(needle, start+len(needle))
        n -= 1
    return start

In [3]:
def bold_resolver(li):
    for i in range(0,len(li)):
        # spaces must be inside if there is any
        val=li[i].strip()
        if val.endswith(','):
            val=val[:-1].rstrip()
        if ('I' in val):
            if (',' not in val):
                if (' ' not in val):
                    val=val[:val.index('I')]+' '+val[val.index('I'):]
            else:
                if(' ' not in val):
                    val=val[:val.index('I')]+' '+val[val.index('I'):].replace(',',', ')
                else:
                    if(', ' in val):
                        val=val[:val.index('I')]+' '+val[val.index('I'):]
                    else:
                        val=val.replace(',',', ')
        elif (',' in val) and (', ' not in val):
            val=val.replace(',',', ')
        if('  ' in val): val=val.replace('  ',' ')
        if('   ' in val): val=val.replace('   ',' ')
        if(val.endswith('I')): val=val+'.'
        li[i]=val.strip()
    return li


In [36]:
from tracemalloc import start

def extract_dict(filename):
    extract_errors=[]
    d = {}
    with pdfplumber.open(filename) as pdf:
        for i in range(14,len(pdf.pages)):
        #for i in range(14,16):
            page = pdf.pages[i]
            #print(i)
            text = page.filter(lambda obj: obj["object_type"] == "char")

            bolds = page.filter(
                lambda obj: obj["object_type"] == "char" and "Bold" in obj["fontname"])
            bolds = bolds.extract_text().split('\n')
            bolds=[item.lstrip().rstrip() for item in bolds if (item!='' and ':' not in item)]   #filter+
            bolds = bold_resolver(bolds)
            if '' in bolds:
                bolds=list(filter(('').__ne__, bolds))
            text = text.extract_text().replace('\n◊',',')
            for i in range(0, len(bolds)):
                try:
                    if (i != len(bolds)-1):
                        #index - space makes sure it wont be find before in another word
                        start = text.index(bolds[i]+' ')+len(bolds[i])
                        end = text.index(bolds[i+1]+' ')
                        
                        if(end > start and i==0):
                            d[bolds[i]] = text[start:end]
                        elif (end > start and i>0):
                            d[bolds[i]] = text[start:end]
                            n=2
                            if((d[bolds[i-1]]!="" and bolds[i-1]!=bolds[i])):
                                new_val=text[start:]
                                while len(d[bolds[i]]) > len(new_val) and start!=-1 and new_val!='':
                                    d[bolds[i]] = new_val
                                    n=n+1
                                    start=find_nth(text,bolds[i]+' ', n)
                                    new_val=text[start:]
                        elif(end<start):
                            d[bolds[i]] = text[start:end]
                            n=1
                            while(d[bolds[i]]==''):
                                n=n+1
                                end = find_nth(text, bolds[i+1], n)
                                d[bolds[i]] = text[start:end]
                    else:
                        start = text.index(bolds[i]+' ')+len(bolds[i])
                        d[bolds[i]] = text[start:]
                        n=2
                    if((d[bolds[i-1]]!="" and bolds[i-1]!=bolds[i])):
                        start=find_nth(text,bolds[i]+' ',n)
                        new_val=text[start:end]
                        while len(d[bolds[i]]) > len(new_val) and start!=-1 and new_val!='':
                            d[bolds[i]] = new_val
                            n=n+1
                            start=find_nth(text,bolds[i]+' ', n)
                            new_val=text[start:end] 
                except Exception as e:
                    extract_errors.append(e)
                    pass
    print("ERRORS OCCURED")
    pp.pprint(extract_errors)
    return d

In [37]:
import pdfplumber
d=extract_dict('szinonimak.pdf')
# runs around 4 min

ERRORS OCCURED
[KeyError('ábrázol'),
 ValueError('substring not found'),
 ValueError('substring not found'),
 KeyError('abnormális, abnormis'),
 KeyError('adagol'),
 KeyError('adósság'),
 KeyError('agg II.'),
 KeyError('ágrólszakadt'),
 KeyError('agyonver'),
 KeyError('ajánlat'),
 KeyError('akadémikus I.'),
 KeyError('akasztó'),
 KeyError('akol'),
 KeyError('alacsony'),
 KeyError('alakzat'),
 KeyError('alapít'),
 ValueError('substring not found'),
 ValueError('substring not found'),
 KeyError('alantas I.'),
 ValueError('substring not found'),
 ValueError('substring not found'),
 KeyError('alapító I.'),
 KeyError('albizottság'),
 KeyError('álhaj'),
 KeyError('alkalmatlanság'),
 KeyError('alkoholtilalom'),
 KeyError('állam'),
 KeyError('állandósul'),
 KeyError('állít'),
 KeyError('álmodozás'),
 KeyError('alsóruha'),
 KeyError('alumínium'),
 KeyError('amiként'),
 KeyError('angolmustár'),
 KeyError('anyó, anyóka'),
 KeyError('áporodott'),
 KeyError('ár2'),
 KeyError('aranykezű'),
 KeyError

In [38]:
# part result
pp.pprint(d)

{'abajgat': ' (ige) ◊ háborgat, zaklat, piszkál, nyaggat, nyúz, bánt, szekál '
            '(biz), szekíroz (biz), molesztál, \n'
            'macerál (biz), vegzál (rég), buzerál (szleng) ♦ BÉKÉN HAGY , '
            '(táj): óbégat, nyivákol, vernyákol (táj) \n',
 'abbahagy': ' (ige) ◊ félbehagy, félbeszakít, félbenszakaszt (rég), '
             'abbaszakít (rég), félbe-szerbe hagy (rég), \n'
             'félretesz, felad, felhagy <vmivel>, elhagy <vmit>, leáll '
             '<vmivel>, megszüntet, megszakít, beszüntet, \n'
             'szüneteltet, megszűnik <vmit tenni>, leszokik <vmiről>, eláll '
             '<vmitől> Sz: leteszi a lantot; szegre \n'
             'akasztja a cipőt; szegre akasztja a kesztyűt; bemondja az '
             'unalmast (szleng); hagyja a fenébe; hagyja a \n'
             'francba; bedobja a törülközőt (szleng) ♦ BEFEJEZ, VÉGIGCSINÁL, '
             'FOLYTAT \n',
 'abbamarad': ' (ige) ◊ félbemarad, félbeszakad, megszakad, megáll, megszűnik, '
          

In [39]:
def opposite_sorter(dict):
    d=dict.copy()
    for key in d.keys():
        # value vill be a list
        d[key] =[item.strip() for item in d[key].split(',')]
        val_li = d[key]

        #type of the key, and first list item
        keytype=''
        if('◊' in val_li[0] and '(' in  val_li[0] and ')' in  val_li[0]):
            keytype=val_li[0][val_li[0].index('('):val_li[0].index(')')+1]

        #rest of the synonymlist
        opp_li=[]
        add_part=[]
        for i in range(1,len(val_li)):
            # skip list item if CAPITAL - opposite, add to remove_list
            if('♦' in val_li[i]):
                parts=val_li[i].split()
                for part in parts:
                    if part!='' and part.isupper():
                        opp_li.append(part.strip().lower())
            if(val_li[i].isupper()):
                opp_li.append(val_li[i].strip().lower())
        # add key type to the word
        if(keytype!=''):
            val_tup=(keytype,opp_li)
            d[key]=val_tup
        # if key type is not known
        else:
            val_tup=('(nem jelölt)',opp_li)
            d[key]=val_tup 
    return d

In [40]:
opposites=opposite_sorter(d)

In [41]:
# remove items which has no opposites 
key_rem_li=[]      
for k,v in opposites.items():
    if not v[1]:
        key_rem_li.append(k)
for k in key_rem_li:
    del opposites[k]

In [42]:
# teszt 2 oldalnyi szinonima kb 400 összehasonlítás
cnt=0
for k,v in opposites.items():
    for e in v[1]:
        cnt=cnt+1
print(cnt)

28423


In [43]:
pp.pprint(opposites)

{'abajgat': ('(ige)', ['békén', 'hagy']),
 'abbahagy': ('(ige)', ['befejez', 'végigcsinál', 'folytat']),
 'abbamarad': ('(ige)', ['folytatódik']),
 'ábránd': ('(fn)', ['valóság', 'realitás']),
 'ábrándos': ('(mn)', ['földhözragadt', 'gyakorlatias', 'realista', 'reális']),
 'abszolút I.': ('(mn)',
                 ['fogyatékos', 'tökéletlen', 'viszonylagos', 'korlátozott']),
 'absztinens': ('(fn és mn)', ['iszákos', 'részeges']),
 'absztrakt': ('(mn)', ['konkrét', 'kézzelfogható']),
 'abszurd': ('(mn)', ['megszokott', 'mindennapi', 'szokványos']),
 'acélos': ('(mn)',
            ['erőtlen', 'puha', 'puhány', 'határozatlan', 'befolyásolható']),
 'ácsorog': ('(ige)', ['megy', 'halad']),
 'ad': ('(ige)', ['kap', 'elvesz', 'kér', 'vesz']),
 'adakozik': ('(ige)', ['kéreget']),
 'adakozó': ('(mn)', ['fösvény', 'szűkmarkú', 'zsugori']),
 'adás': ('(fn)', ['vétel']),
 'ádáz': ('(mn)', ['békés', 'nyugodt', 'szelíd']),
 'afelé': ('(hsz)', ['afelől', 'onnan']),
 'afelől': ('(hsz)', ['ettől', 'ezér

In [47]:
# synonyms[key][0] - type
# synonyms[key][1] - synonymlist

types={}
for key in opposites:
    types[opposites[key][0]]=types.get(opposites[key][0],0)+1
#sort
types={k: v for k, v in sorted(types.items(), key=lambda item: item[1])}
pp.pprint(types)

{'(isz)': 1,
 '(hsz és nm)': 1,
 '(hat-ragos nm)': 1,
 '(hsz és ksz)': 1,
 '(ragos fn)': 1,
 '(táj)': 2,
 '(nu és hsz)': 2,
 '(ksz)': 3,
 '(fn  és  mn)': 3,
 '(mn  és  fn)': 3,
 '(msz)': 4,
 '(nu)': 6,
 '(fn és mn)': 18,
 '(szn)': 20,
 '(nm)': 42,
 '(mn és fn)': 111,
 '(nem jelölt)': 134,
 '(hsz)': 491,
 '(fn)': 2310,
 '(mn)': 3193,
 '(ige)': 3729}


In [48]:
cnt=0
for k, v in opposites.items():
    cnt=cnt+1
    for e in v[1]:
        cnt=cnt+1
print(cnt)

38499


In [21]:
#export to json
import json 

with open('ellentetek.json','w', encoding='utf8') as output:
    json.dump(opposites, output, indent=2, ensure_ascii=False)